In [1]:
import numpy as np
from scipy import integrate
from tqdm.auto import trange
import tqdm
import torch
import sys

$$\int_{-1}^{1} \int_{-1}^{1} \int_{-1}^{1} \sin (z-x) \cos ^{2}(z+y)(x-y+z) dz d y d x \approx 0.372854$$

In [2]:
f = lambda z, y, x: np.sin(z-x) * np.cos(z+y) ** 2 * (x-y+z)
integrate.tplquad(f, -1, 1, lambda x: -1, lambda x: 1,
                  lambda x, y: -1, lambda x, y: 1)

(0.3728540400817617, 1.5648351097112007e-14)

In [3]:
%cd /home/kevin/AutoInt
from src.utils import get_device
from src.integration.autoint import *
from src.experiment.autoint3d import *

device = get_device(free=False, min_ram=0)

/home/kevin/AutoInt


In [4]:
"""
Wrap x, f(x) for x in R^n
"""
class NDWrapper(torch.utils.data.Dataset):
    def __init__(self, ranges, fn, sampling_density):
        self.dim = len(ranges)
        self.X = torch.rand((sampling_density, self.dim))
        self.scale = torch.tensor(ranges)
        self.X *= (self.scale[:, 1] - self.scale[:, 0])
        self.X += self.scale[:, 0]
        self.f = fn(self.X)

        self.X = self.X.float().to(device)
        self.f = self.f.float().to(device)

    def __len__(self):
        return len(self.X)

    def __getitem__(self, idx):
        return self.X[idx], self.f[idx]


In [5]:
from torch.utils.data import DataLoader

def func_to_fit(X):
    x = X[:, 0]
    y = X[:, 1]
    z = X[:, 2]
    return torch.sin(z-x) * torch.cos(z+y) ** 2 * (x-y+z)

dataset = NDWrapper([[-1,1],[-1,1], [-1,1]], fn=func_to_fit, sampling_density=1024)

dataloader = DataLoader(dataset, shuffle=True, batch_size=64)

## Gauss's Divergence Theorem

$$
\iiint_{\Omega}\left(\frac{\partial P}{\partial x}+\frac{\partial Q}{\partial y}+\frac{\partial R}{\partial z}\right) d v=\iint_{\Sigma} P d y d z+Q d z d x+R d x d y \\

\begin{align*}
\int_C(L\,dx+M\,dy)
&= L_{ad}(1, -1) - L_{ad}(-1, -1) + M_{ad}(1, 1) - M_{ad}(1, -1)  \\
&+ L_{ad}(-1, 1) - L_{ad}(1, 1) + M_{ad}(-1, -1) - M_{ad}(-1, 1)
\end{align*}
$$

Set $\dfrac{\partial M_R}{\partial x} - \dfrac{\partial L_R}{\partial y} $ to $R$, then $\int R dx dy$ can be computed as $\int_C(L_R\,dx+M_R\,dy)$

$\dfrac{\partial R}{\partial z}$ is then $\dfrac{\partial^2 M_R}{\partial x \partial z} - \dfrac{\partial^2 L_R}{\partial y \partial z}$. The network is $\int L_R dx$, the derivative is $\dfrac{\partial^3 \int L_R dx}{\partial x \partial y \partial z}$

In [47]:
LRx = MLPnD(MixSequential, 3, nn.Tanh()).to(device)
MRy = MLPnD(MixSequential, 3, nn.Tanh()).to(device)
LQz = MLPnD(MixSequential, 3, nn.Tanh()).to(device)
MQx = MLPnD(MixSequential, 3, nn.Tanh()).to(device)
LPy = MLPnD(MixSequential, 3, nn.Tanh()).to(device)
MPz = MLPnD(MixSequential, 3, nn.Tanh()).to(device)


In [49]:
loss_func = nn.MSELoss()
params = list(LRx.parameters()) + list(MRy.parameters()) + list(LQz.parameters()) + list(MQx.parameters()) + list(LPy.parameters()) + list(MPz.parameters())
optimizer = torch.optim.Adam(params, lr=5e-3)
scheduler = torch.optim.lr_scheduler.StepLR(optimizer, step_size=20, gamma=0.5)

for epoch in trange(0, 200, position=0, leave=True):
    current_loss = []

    for i, (x, f) in enumerate(dataloader):
        optimizer.zero_grad()

        # Compute loss
        loss = loss_func(MRy.dnforward(x, [0, 1, 2]) - LRx.dnforward(x, [0, 1, 2])
                       + MQx.dnforward(x, [0, 1, 2]) - LQz.dnforward(x, [0, 1, 2])
                       + MPz.dnforward(x, [0, 1, 2]) - LPy.dnforward(x, [0, 1, 2]), f)

        # Perform backward pass
        loss.backward()

        # Perform optimization
        optimizer.step()

        # Print statistics
        current_loss.append(loss.item())

    print(f'Epoch {epoch} \t Loss: {sum(current_loss) / len(current_loss)}')

    scheduler.step()

  0%|          | 0/200 [00:00<?, ?it/s]

Epoch 0 	 Loss: 0.14101790612039622
Epoch 1 	 Loss: 0.018408627569442615
Epoch 2 	 Loss: 0.005929167731665075
Epoch 3 	 Loss: 0.003388515207916498
Epoch 4 	 Loss: 0.0014494275237666443
Epoch 5 	 Loss: 0.0013290060924191494
Epoch 6 	 Loss: 0.0011965918929490726
Epoch 7 	 Loss: 0.0011820480503956787
Epoch 8 	 Loss: 0.0009939478950400371
Epoch 9 	 Loss: 0.0009383028973388718
Epoch 10 	 Loss: 0.0010461210913490504
Epoch 11 	 Loss: 0.001177046917291591
Epoch 12 	 Loss: 0.0010589019857434323
Epoch 13 	 Loss: 0.0007246474269777536
Epoch 14 	 Loss: 0.0005221886094659567
Epoch 15 	 Loss: 0.00032829001702339156
Epoch 16 	 Loss: 0.0003301674178146641
Epoch 17 	 Loss: 0.00027743319060391514
Epoch 18 	 Loss: 0.0004356449353508651
Epoch 19 	 Loss: 0.0005534748052014038
Epoch 20 	 Loss: 0.0005430706933111651
Epoch 21 	 Loss: 0.00036765862114407355
Epoch 22 	 Loss: 0.00018995166374224937
Epoch 23 	 Loss: 0.00015322337276302278
Epoch 24 	 Loss: 0.00010072055192722473
Epoch 25 	 Loss: 9.055417740455596e

In [50]:
LRx.eval()
MRy.eval()
LQz.eval()
MQx.eval()
LPy.eval()
MPz.eval()


MLPnD(
  (layers): MixSequential(
    (layers): MultSequential(
      (0): Linear(in_features=3, out_features=128, bias=True)
      (1): Tanh()
      (2): Linear(in_features=128, out_features=128, bias=True)
      (3): Tanh()
      (4): Linear(in_features=128, out_features=128, bias=True)
      (5): Tanh()
      (6): Linear(in_features=128, out_features=1, bias=True)
    )
  )
)

In [51]:
from scipy import integrate
f = lambda z, y, x: MRy.dnforward(torch.tensor([x, y, z]).to(device), [0, 1, 2]) \
                    - LRx.dnforward(torch.tensor([x, y, z]).to(device), [0, 1, 2])
integrate.tplquad(f, -1, 1, lambda x: -1, lambda x: 1,
                  lambda x, y: -1, lambda x, y: 1, epsabs=1e-3)

(0.3534203591398006, 0.0004611033335972816)

In [52]:
from scipy import integrate
f1 = lambda y, x: MRy.dnforward(torch.tensor([x, y, 1.]).to(device), [0, 1]).item() \
                - LRx.dnforward(torch.tensor([x, y, 1.]).to(device), [0, 1]).item()
f2 = lambda y, x: MRy.dnforward(torch.tensor([x, y, -1.]).to(device), [0, 1]).item() \
                - LRx.dnforward(torch.tensor([x, y, -1.]).to(device), [0, 1]).item()
up = integrate.dblquad(f1, -1, 1, lambda x: -1, lambda x: 1)[0]
down = integrate.dblquad(f2, -1, 1, lambda x: -1, lambda x: 1)[0]
print(up, down, up - down)

-0.06486284626232106 -0.41828318857225133 0.35342034230993025


In [53]:
endpoints = torch.tensor([[-1., -1], [-1, 1], [1, -1], [1, 1]]).to(device)
res = 0

endpoints_ = torch.cat([endpoints, torch.ones(4, 1).to(endpoints)], -1)
m = MRy(endpoints_)
l = LRx(endpoints_)
res += l[2] - l[0] + m[3] - m[2] + l[1] - l[3] + m[0] - m[1]

print(res)

endpoints_ = torch.cat([endpoints, -torch.ones(4, 1).to(endpoints)], -1)
m = MRy(endpoints_)
l = LRx(endpoints_)
res -= l[2] - l[0] + m[3] - m[2] + l[1] - l[3] + m[0] - m[1]
print(res)

tensor(-0.0649, device='cuda:0', grad_fn=<AddBackward0>)
tensor(0.3534, device='cuda:0', grad_fn=<SubBackward0>)


In [54]:
from scipy import integrate
f = lambda z, y, x: MQx.dnforward(torch.tensor([x, y, z]).to(device), [0, 1, 2]) \
                    - LQz.dnforward(torch.tensor([x, y, z]).to(device), [0, 1, 2])
integrate.tplquad(f, -1, 1, lambda x: -1, lambda x: 1,
                  lambda x, y: -1, lambda x, y: 1, epsabs=1e-3)

(-0.3918889044716073, 0.0005438110088230398)

In [55]:
from scipy import integrate
f1 = lambda z, x: MQx.dnforward(torch.tensor([x, 1., z]).to(device), [0, 2]).item() \
                - LQz.dnforward(torch.tensor([x, 1., z]).to(device), [0, 2]).item()
f2 = lambda z, x: MQx.dnforward(torch.tensor([x, -1., z]).to(device), [0, 2]).item() \
                - LQz.dnforward(torch.tensor([x, -1., z]).to(device), [0, 2]).item()
up = integrate.dblquad(f1, -1, 1, lambda x: -1, lambda x: 1)[0]
down = integrate.dblquad(f2, -1, 1, lambda x: -1, lambda x: 1)[0]
print(up, down, up - down)

-0.37398485147961685 0.017904033097334807 -0.39188888457695165


In [56]:
res = 0

endpoints_ = torch.cat([endpoints[:, :1], torch.ones(4, 1).to(endpoints), endpoints[:, -1:]], -1)
m = LQz(endpoints_)
l = MQx(endpoints_)
res -= l[2] - l[0] + m[3] - m[2] + l[1] - l[3] + m[0] - m[1]

endpoints_ = torch.cat([endpoints[:, :1], - torch.ones(4, 1).to(endpoints), endpoints[:, -1:]], -1)
m = LQz(endpoints_)
l = MQx(endpoints_)
res += l[2] - l[0] + m[3] - m[2] + l[1] - l[3] + m[0] - m[1]

print(res)

tensor(-0.3919, device='cuda:0', grad_fn=<AddBackward0>)


In [57]:
from scipy import integrate
f = lambda z, y, x: MPz.dnforward(torch.tensor([x, y, z]).to(device), [0, 1, 2]) \
                    - LPy.dnforward(torch.tensor([x, y, z]).to(device), [0, 1, 2])
integrate.tplquad(f, -1, 1, lambda x: -1, lambda x: 1,
                  lambda x, y: -1, lambda x, y: 1, epsabs=1e-3)

(0.40992560821251967, 5.437761449347213e-06)

In [58]:
from scipy import integrate
f1 = lambda z, y: MPz.dnforward(torch.tensor([1., y, z]).to(device), [1, 2]).item() \
                - LPy.dnforward(torch.tensor([1., y, z]).to(device), [1, 2]).item()
f2 = lambda z, y: MPz.dnforward(torch.tensor([-1., y, z]).to(device), [1, 2]).item() \
                - LPy.dnforward(torch.tensor([-1., y, z]).to(device), [1, 2]).item()
up = integrate.dblquad(f1, -1, 1, lambda x: -1, lambda x: 1)[0]
down = integrate.dblquad(f2, -1, 1, lambda x: -1, lambda x: 1)[0]
print(up, down, up - down)

-0.03384992164775824 -0.4437755149791509 0.40992559333139267


In [59]:
res = 0

endpoints_ = torch.cat([torch.ones(4, 1).to(endpoints), endpoints], -1)
m = LPy(endpoints_)
l = MPz(endpoints_)
res -= l[2] - l[0] + m[3] - m[2] + l[1] - l[3] + m[0] - m[1]

endpoints_ = torch.cat([- torch.ones(4, 1).to(endpoints), endpoints], -1)
m = LPy(endpoints_)
l = MPz(endpoints_)
res += l[2] - l[0] + m[3] - m[2] + l[1] - l[3] + m[0] - m[1]

print(res)

tensor(0.4099, device='cuda:0', grad_fn=<AddBackward0>)


In [60]:
endpoints = torch.tensor([[-1., -1], [-1, 1], [1, -1], [1, 1]]).to(device)
res = 0

endpoints_ = torch.cat([endpoints, torch.ones(4, 1).to(endpoints)], -1)
m = MRy(endpoints_)
l = LRx(endpoints_)
res += l[2] - l[0] + m[3] - m[2] + l[1] - l[3] + m[0] - m[1]

endpoints_ = torch.cat([endpoints, -torch.ones(4, 1).to(endpoints)], -1)
m = MRy(endpoints_)
l = LRx(endpoints_)
res -= l[2] - l[0] + m[3] - m[2] + l[1] - l[3] + m[0] - m[1]

endpoints_ = torch.cat([endpoints[:, :1], torch.ones(4, 1).to(endpoints), endpoints[:, -1:]], -1)
m = LQz(endpoints_)
l = MQx(endpoints_)
res -= l[2] - l[0] + m[3] - m[2] + l[1] - l[3] + m[0] - m[1]

endpoints_ = torch.cat([endpoints[:, :1], - torch.ones(4, 1).to(endpoints), endpoints[:, -1:]], -1)
m = LQz(endpoints_)
l = MQx(endpoints_)
res += l[2] - l[0] + m[3] - m[2] + l[1] - l[3] + m[0] - m[1]

endpoints_ = torch.cat([torch.ones(4, 1).to(endpoints), endpoints], -1)
m = LPy(endpoints_)
l = MPz(endpoints_)
res -= l[2] - l[0] + m[3] - m[2] + l[1] - l[3] + m[0] - m[1]

endpoints_ = torch.cat([- torch.ones(4, 1).to(endpoints), endpoints], -1)
m = LPy(endpoints_)
l = MPz(endpoints_)
res += l[2] - l[0] + m[3] - m[2] + l[1] - l[3] + m[0] - m[1]

In [61]:
print(res)

tensor(0.3715, device='cuda:0', grad_fn=<AddBackward0>)


In [81]:
def cuboid(xa, xb, ya, yb, za, zb):
    return  torch.tensor([[xa, ya, zb],
                          [xa, yb, zb],
                          [xb, ya, zb],
                          [xb, yb, zb],
                          [xa, ya, za],
                          [xa, yb, za],
                          [xb, ya, za],
                          [xb, yb, za],
                          [xa, yb, za],
                          [xa, yb, zb],
                          [xb, yb, za],
                          [xb, yb, zb],
                          [xa, ya, za],
                          [xa, ya, zb],
                          [xb, ya, za],
                          [xb, ya, zb],
                          [xb, ya, za],
                          [xb, ya, zb],
                          [xb, yb, za],
                          [xb, yb, zb],
                          [xa, ya, za],
                          [xa, ya, zb],
                          [xa, yb, za],
                          [xa, yb, zb]]).to(device)

scale = 1.
endpoints = cuboid(-.5, .5, -.7, .7, -.9, .9)
res = 0

endpoints_ = endpoints[:4]
m = MRy(endpoints_)
l = LRx(endpoints_)
res += l[2] - l[0] + m[3] - m[2] + l[1] - l[3] + m[0] - m[1]

endpoints_ = endpoints[4:8]
m = MRy(endpoints_)
l = LRx(endpoints_)
res -= l[2] - l[0] + m[3] - m[2] + l[1] - l[3] + m[0] - m[1]

endpoints_ = endpoints[8:12]
m = LQz(endpoints_)
l = MQx(endpoints_)
res -= l[2] - l[0] + m[3] - m[2] + l[1] - l[3] + m[0] - m[1]

endpoints_ = endpoints[12:16]
m = LQz(endpoints_)
l = MQx(endpoints_)
res += l[2] - l[0] + m[3] - m[2] + l[1] - l[3] + m[0] - m[1]

endpoints_ = endpoints[16:20]
m = LPy(endpoints_)
l = MPz(endpoints_)
res -= l[2] - l[0] + m[3] - m[2] + l[1] - l[3] + m[0] - m[1]

endpoints_ = endpoints[20:]
m = LPy(endpoints_)
l = MPz(endpoints_)
res += l[2] - l[0] + m[3] - m[2] + l[1] - l[3] + m[0] - m[1]

print(res)

tensor(0.3342, device='cuda:0', grad_fn=<AddBackward0>)


In [82]:
f = lambda z, y, x: np.sin(z-x) * np.cos(z+y) ** 2 * (x-y+z)
integrate.tplquad(f, -.5, .5, lambda x: -.7, lambda x: .7,
                  lambda x, y: -.9, lambda x, y: .9)

(0.3339726595741636, 5.808053701607837e-15)

# Simplified Version

In [6]:
from IPython.display import SVG, display

def imshow(fig):
    return display(SVG(fig.to_image(format="svg")))

In [7]:
ReQU = [lambda _, x: torch.where(x > 0., 0.125 * x ** 2 + 0.5 * x + np.log(2.), torch.log(torch.exp(x) + 1.)),
        lambda _, x: torch.where(x > 0., 0.25 * x + 0.5, 1. / (1. + torch.exp(-x))),
        lambda _, x: torch.where(x > 0., 0.25 * torch.ones_like(x), torch.exp(-x) / (1 + torch.exp(-x)) ** 2),
        lambda _, x: torch.where(x > 0., torch.zeros_like(x),
                                 - torch.exp(x) * (torch.exp(x) - 1.) / (1. + torch.exp(x)) ** 3)]

In [8]:
import plotly.graph_objects as go

x = torch.arange(-3., 3., 0.001)
d0 = ReQU[0](None, x)
d1 = ReQU[1](None, x)
d2 = ReQU[2](None, x)
d3 = ReQU[3](None, x)

fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=d0, mode='markers', name='d0', marker_size=4))
fig.add_trace(go.Scatter(x=x, y=d1, mode='markers', name='d1', marker_size=4))
fig.add_trace(go.Scatter(x=x, y=d2, mode='markers', name='d2', marker_size=4))
fig.add_trace(go.Scatter(x=x, y=d3, mode='markers', name='d3', marker_size=4))

fig.update_layout(
    title=r"The ReQU (quadratic unit) activation",
    xaxis_title="x",
    yaxis_title="f",
)

imshow(fig)

In [17]:
from src.integration.autoint import ReQU

L = MLPnD(MixSequential, 3, ReQU()).to(device)
M = MLPnD(MixSequential, 3, ReQU()).to(device)

loss_func = nn.MSELoss()
params = list(L.parameters()) + list(M.parameters())
optimizer = torch.optim.Adam(params, lr=5e-3)
scheduler = torch.optim.lr_scheduler.StepLR(optimizer, step_size=20, gamma=0.5)

for epoch in trange(0, 200):

    current_loss = []

    for i, (x, f) in enumerate(dataloader):
        optimizer.zero_grad()

        # Compute loss
        loss = loss_func(M.dnforward(x, [0, 1, 2]) * 3 - L.dnforward(x, [0, 1, 2]) * 3, f)

        # Perform backward pass
        loss.backward()

        # Perform optimization
        optimizer.step()

        # Print statistics
        current_loss.append(loss.item())

    print(f'Epoch {epoch} \t Loss: {sum(current_loss) / len(current_loss)}', file=sys.stderr)

    scheduler.step()


  0%|          | 0/200 [00:00<?, ?it/s]

Epoch 0 	 Loss: 0.15392274409532547
Epoch 1 	 Loss: 0.10571955796331167
Epoch 2 	 Loss: 0.07095159264281392
Epoch 3 	 Loss: 0.05296450771857053
Epoch 4 	 Loss: 0.028838836820796132
Epoch 5 	 Loss: 0.022281613491941243
Epoch 6 	 Loss: 0.018274135421961546
Epoch 7 	 Loss: 0.013863540720194578
Epoch 8 	 Loss: 0.010958353785099462
Epoch 9 	 Loss: 0.009170531091513112
Epoch 10 	 Loss: 0.010604629060253501
Epoch 11 	 Loss: 0.008234456821810454
Epoch 12 	 Loss: 0.006930497474968433
Epoch 13 	 Loss: 0.0061525685305241495
Epoch 14 	 Loss: 0.005374599262722768
Epoch 15 	 Loss: 0.005075248802313581
Epoch 16 	 Loss: 0.004183789307717234
Epoch 17 	 Loss: 0.0041031424480024725
Epoch 18 	 Loss: 0.00361379656533245
Epoch 19 	 Loss: 0.003051704479730688
Epoch 20 	 Loss: 0.0027033372170990333
Epoch 21 	 Loss: 0.0023947647496243007
Epoch 22 	 Loss: 0.0024460122076561674
Epoch 23 	 Loss: 0.0023325339643633924
Epoch 24 	 Loss: 0.0020359302943688817
Epoch 25 	 Loss: 0.0022387438293662854
Epoch 26 	 Loss: 0.

In [18]:
def nested_stack(tensors):
    """
    Stack a nested list of tensors by considering each level as a new dimension at dim0

    :param tensors: a nested list of tensors
    :return: the concatenated tensor
    """
    if type(tensors) == torch.Tensor:
        return tensors
    elif type(tensors) == float:
        return torch.tensor(tensors)
    else:
        assert type(tensors) == list
        return torch.stack([nested_stack(tl) for tl in tensors], 0)


## First derivative

In [22]:
f = lambda z, y, x: M.dnforward(torch.tensor([x, y, z]).to(device), [0, 1, 2]).item() * 3 \
                  - L.dnforward(torch.tensor([x, y, z]).to(device), [0, 1, 2]).item() * 3
integrate.tplquad(f, -.5, .5, lambda x: -.7, lambda x: .7,
                  lambda x, y: -.9, lambda x, y: .9)

/home/kevin/miniconda3/envs/autoint/lib/python3.9/site-packages/scipy/integrate/_quadpack_py.py:879: IntegrationWarning:

The maximum number of subdivisions (50) has been achieved.
  If increasing the limit yields no improvement it is advised to analyze 
  the integrand in order to determine the difficulties.  If the position of a 
  local difficulty can be determined (singularity, discontinuity) one will 
  probably gain from splitting up the interval and calling the integrator 
  on the subranges.  Perhaps a special-purpose integrator should be used.



KeyboardInterrupt: 

In [21]:
def cuboid(xa, xb, ya, yb, za, zb):
    return  nested_stack( [[xa, ya, zb],
                           [xa, yb, zb],
                           [xb, ya, zb],
                           [xb, yb, zb],
                           [xa, ya, za],
                           [xa, yb, za],
                           [xb, ya, za],
                           [xb, yb, za],
                           [xa, yb, za],
                           [xa, yb, zb],
                           [xb, yb, za],
                           [xb, yb, zb],
                           [xa, ya, za],
                           [xa, ya, zb],
                           [xb, ya, za],
                           [xb, ya, zb],
                           [xb, ya, za],
                           [xb, ya, zb],
                           [xb, yb, za],
                           [xb, yb, zb],
                           [xa, ya, za],
                           [xa, ya, zb],
                           [xa, yb, za],
                           [xa, yb, zb]]).to(device)

fac = torch.stack([torch.ones(8)], 0)

endpoints = cuboid(-.5 * fac, .5 * fac,
                   -.7 * fac, .7 * fac,
                   -.9 * fac, .9 * fac).view(3, 2, 4, 3, -1).transpose(-1, -2)

m = M(endpoints).sum(0)
m = m[0] - m[1]
l = L(endpoints).sum(0)
l = l[0] - l[1]

res = l[2] - l[0] + m[3] - m[2] + l[1] - l[3] + m[0] - m[1]
#res.view(2, 8)
res

tensor([0.3320, 0.3320, 0.3320, 0.3320, 0.3320, 0.3320, 0.3320, 0.3320],
       device='cuda:0', grad_fn=<SubBackward0>)

In [196]:
f = lambda y, x: M.dnforward(torch.tensor([x, y, .2]).to(device), [0, 1, 2]) * 3 \
               - L.dnforward(torch.tensor([x, y, .2]).to(device), [0, 1, 2]) * 3

integrate.dblquad(f, -.25, .25, lambda x: -.35, lambda x: .35)

(0.005617444973813698, 1.2558851537501944e-08)

In [201]:
def rectangle(xa, xb, ya, yb, z):
    xa = xa * torch.ones_like(z)
    xb = xb * torch.ones_like(z)
    ya = ya * torch.ones_like(z)
    yb = yb * torch.ones_like(z)

    return  nested_stack( [[xa, ya, z],
                           [xa, yb, z],
                           [xb, ya, z],
                           [xb, yb, z]]).to(device)


In [204]:
m = M.dnforward(rectangle(-.25, .25, -.35, .35, .2 * torch.ones(8).to(device)).to(device).transpose(-1, -2), [2]) * 3
l = L.dnforward(rectangle(-.25, .25, -.35, .35, .2 * torch.ones(8).to(device)).to(device).transpose(-1, -2), [2]) * 3
l[2] - l[0] + m[3] - m[2] + l[1] - l[3] + m[0] - m[1]

tensor([0.0056, 0.0056, 0.0056, 0.0056, 0.0056, 0.0056, 0.0056, 0.0056],
       device='cuda:0', grad_fn=<SubBackward0>)

In [203]:
rectangle(-.25, .25, -.35, .35, .2 * torch.ones(8).to(device)).shape


torch.Size([4, 3, 8])

## Integrated Version

In [6]:
# from src.integration.autoint import Cuboid

cub = Cuboid().to(device)
cub.L.layers.layers[1] = nn.Tanh()
cub.L.layers.layers[3] = nn.Tanh()
cub.L.layers.layers[5] = nn.Tanh()
cub.M.layers.layers[1] = nn.Tanh()
cub.M.layers.layers[3] = nn.Tanh()
cub.M.layers.layers[5] = nn.Tanh()
loss_func = nn.MSELoss()
params = cub.parameters()
optimizer = torch.optim.Adam(params, lr=5e-3)
scheduler = torch.optim.lr_scheduler.StepLR(optimizer, step_size=20, gamma=0.5)

for epoch in trange(0, 200):

    current_loss = []

    for i, (x, f) in enumerate(dataloader):
        optimizer.zero_grad()

        # Compute loss
        loss = loss_func(cub(x), f)

        # Perform backward pass
        loss.backward()

        # Perform optimization
        optimizer.step()

        # Print statistics
        current_loss.append(loss.item())

    print(f'Epoch {epoch} \t Loss: {sum(current_loss) / len(current_loss)}', file=sys.stderr)

    scheduler.step()


  0%|          | 0/200 [00:00<?, ?it/s]

Epoch 0 	 Loss: 0.1004777904599905
Epoch 1 	 Loss: 0.03199167468119413
Epoch 2 	 Loss: 0.01476145617198199
Epoch 3 	 Loss: 0.007016058429144323
Epoch 4 	 Loss: 0.005459339779918082
Epoch 5 	 Loss: 0.005309090091031976
Epoch 6 	 Loss: 0.0039179389423225075
Epoch 7 	 Loss: 0.0023726329673081636
Epoch 8 	 Loss: 0.001330688850430306
Epoch 9 	 Loss: 0.0010344479342165869
Epoch 10 	 Loss: 0.0012696955163846724
Epoch 11 	 Loss: 0.0005853767888766015
Epoch 12 	 Loss: 0.0008689305468578823
Epoch 13 	 Loss: 0.0013051672322035301
Epoch 14 	 Loss: 0.0008084167748165783
Epoch 15 	 Loss: 0.0010297458356944844
Epoch 16 	 Loss: 0.0012045845396642108
Epoch 17 	 Loss: 0.0009025784038385609
Epoch 18 	 Loss: 0.0016662476082274225
Epoch 19 	 Loss: 0.0018456733159837313
Epoch 20 	 Loss: 0.0010495957649254706
Epoch 21 	 Loss: 0.0005384887881518807
Epoch 22 	 Loss: 0.00039430866127077024
Epoch 23 	 Loss: 0.00031284894885175163
Epoch 24 	 Loss: 0.0002688781496544834
Epoch 25 	 Loss: 0.0003243045621275087
Epoch

In [14]:
f = lambda z, y, x: cub.M.dnforward(torch.tensor([x, y, z]).to(device), [0, 1, 2]) * 3 \
                  - cub.L.dnforward(torch.tensor([x, y, z]).to(device), [0, 1, 2]) * 3
integrate.tplquad(f, -.25, .75, lambda x: -.35, lambda x: .65,
                  lambda x, y: -.45, lambda x, y: .45)

(-0.0252408625727742, 1.4838603022549818e-08)

In [13]:
f = lambda z, y, x: cub.M.dnforward(torch.tensor([x, y, z]).to(device), [0, 1, 2]) * 3 \
                  - cub.L.dnforward(torch.tensor([x, y, z]).to(device), [0, 1, 2]) * 3
integrate.tplquad(f, -.45, .55, lambda x: -.25, lambda x: .75,
                  lambda x, y: -.35, lambda x, y: .35)

(-0.013877258589221298, 1.4785626916671277e-08)

In [15]:
f = lambda y, x: cub.M.dnforward(torch.tensor([x, y, .45]).to(device), [0, 1, 2]) * 3 \
               - cub.L.dnforward(torch.tensor([x, y, .45]).to(device), [0, 1, 2]) * 3

integrate.dblquad(f, -.25, .75, lambda x: -.35, lambda x: .65)

/home/kevin/miniconda3/envs/autoint/lib/python3.9/site-packages/scipy/integrate/_quadpack_py.py:879: IntegrationWarning:

The occurrence of roundoff error is detected, which prevents 
  the requested tolerance from being achieved.  The error may be 
  underestimated.



(0.030776780023124166, 3.137097331906702e-08)

In [8]:
f(0.0)

array([-0.09728324, -0.0640161 ], dtype=float32)

In [11]:
f = lambda x: cub.lamb_t(torch.Tensor([[.25, .35], [.45, .25]]).to(device), torch.tensor([x, x]).to(device)).cpu().detach()

integrate.quad_vec(f, -.35, .35)

KeyboardInterrupt: 

In [13]:
(np.random.rand() - 0.5) * .35

0.026030918476549703

In [22]:
res = 0.
N = 100000
for _ in trange(N):
    x = (np.random.rand() - 0.5) * 2 * .35
    y = (np.random.rand() - 0.5) * 2 * .45
    res += cub.lamb_t(torch.Tensor([[.25, .35], [.45, .25]]).to(device), torch.tensor([x, y]).to(device))

  0%|          | 0/100000 [00:00<?, ?it/s]

In [23]:
res = res / N * torch.Tensor([0.7, 0.9]).to(device)
res

tensor([-0.0374,  0.0048], device='cuda:0', grad_fn=<MulBackward0>)

In [16]:
f = lambda y, x: cub.M.dnforward(torch.tensor([x, y, .35]).to(device), [0, 1, 2]) * 3 \
               - cub.L.dnforward(torch.tensor([x, y, .35]).to(device), [0, 1, 2]) * 3

integrate.dblquad(f, -.45, .55, lambda x: -.25, lambda x: .75)

(-0.0017464963478737803, 5.903847639638909e-08)

In [7]:
cub.lamb_t(torch.Tensor([[.25, .35], [.45, .25]]).to(device), torch.Tensor([.45, .35]).to(device))

tensor([ 0.0308, -0.0017], device='cuda:0', grad_fn=<SubBackward0>)

In [10]:
cub.int_lamb(torch.Tensor([[.25, .35], [.45, .25]]).to(device), torch.Tensor([-.45, -.35]).to(device), torch.Tensor([.45, .35]).to(device))


tensor([-0.0252, -0.0139], device='cuda:0', grad_fn=<SubBackward0>)

In [19]:
cub.int_lamb(torch.Tensor([[.25, .35], [.45, .25]]).to(device), torch.Tensor([-.35, -.45]).to(device), torch.Tensor([.35, .45]).to(device))

tensor([-0.0375,  0.0047], device='cuda:0', grad_fn=<SubBackward0>)